In [1]:
import os,sys
import tensorflow as tf
# import importlib
sys.path.append('/home/ubuntu/hacking/projects/deep-mediation/nov2020')
import auxiliaryfunctions
# importlib.reload(auxiliaryfunctions)
import statsmodels.api as sm
import statsmodels.formula.api as smf
import seaborn as sns
import numpy as np
from scipy.stats import zscore,norm
from keras.callbacks import EarlyStopping
import matplotlib.pyplot as plt
import os
import pandas as pd
import random as python_random

from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error,make_scorer,mean_absolute_error,r2_score

# from datagenerator import dataGenerator
from keras import backend as K

from tensorflow.keras.callbacks import LearningRateScheduler, ModelCheckpoint, EarlyStopping
from keras.optimizers import Adam, SGD


Bad key savefig.frameon in file /home/ubuntu/anaconda3/envs/deep_structure/lib/python3.6/site-packages/matplotlib/mpl-data/stylelib/_classic_test.mplstyle, line 421 ('savefig.frameon : True')
You probably need to get an updated matplotlibrc file from
https://github.com/matplotlib/matplotlib/blob/v3.3.3/matplotlibrc.template
or from the matplotlib source distribution

Bad key verbose.level in file /home/ubuntu/anaconda3/envs/deep_structure/lib/python3.6/site-packages/matplotlib/mpl-data/stylelib/_classic_test.mplstyle, line 472 ('verbose.level  : silent      # one of silent, helpful, debug, debug-annoying')
You probably need to get an updated matplotlibrc file from
https://github.com/matplotlib/matplotlib/blob/v3.3.3/matplotlibrc.template
or from the matplotlib source distribution

Bad key verbose.fileo in file /home/ubuntu/anaconda3/envs/deep_structure/lib/python3.6/site-packages/matplotlib/mpl-data/stylelib/_classic_test.mplstyle, line 473 ('verbose.fileo  : sys.stdout  # a log filen

In [2]:
np.random.seed(123)
python_random.seed(123)
tf.random.set_seed(1234)

early_stopping = True
epochs = 1000
batch_size = 4
use_dynamic_LR=False
# optimizer='Adam'
algo = 'deep' #['shallow','deep','svr'] 
patience = 50
result_path = '/home/ubuntu/hacking/projects/deep-mediation/nov2020/results/simulation-2-results'
num_subs = 1000
num_iters = 20
num_runs = 100
new_shape = [[32,32]]

In [3]:
def make_plot(z,m,d,iter):
    plt.figure(figsize=(20,5))
    plt.subplot(1, 4, 1)
    plot_distribution(z,m,labels=['z','m'])

    plt.subplot(1, 4, 2)
    plot_distribution(z,d,labels=['z','d'])

    plt.subplot(1, 4, 3)
    plot_scatter(z,d,labels= ['z','d'])

    plt.subplot(1, 4, 4)
    plot_scatter(z,m,labels= ['z','m'])
    # plt.savefig(os.path.join(result_path,'result'+ str(iter) +'.png'),dpi=300)
    plt.show()

def plot_distribution(z,m,labels):
    sns.distplot(z, hist=True, rug=True,label=labels[0]);
    sns.distplot(m, hist=True, rug=True,label=labels[1]);
    plt.legend()

def plot_scatter(y_test,y_pred,labels):
    r = np.corrcoef(y_pred,y_test)[0,1]
    r = round(r,3)
    plt.scatter(y_test,y_pred)
    plt.xlabel(labels[0])
    plt.ylabel(labels[1])
    plt.title('r=%s'%r)

def plot_loss(history):
    plt.plot(history.history['loss'])
    plt.plot(history.history['val_loss'])
    plt.title('model loss')
    plt.ylabel('MSE')
    plt.xlabel('epoch')
    plt.legend(['train', 'val'], loc='upper left')
    plt.show()

def plot_error(ax,values,title,y_lab,num_iterations):
    ax.plot(values)
    ax.set_xlim([0,num_iterations])
    ax.set_xlabel('#iterations')
    ax.set_ylabel(y_lab)
    ax.set_title(title)

def create_empty_df(num_runs,num_iters):
    # Creates an empty dataFrame
    a = np.empty((num_runs,num_iters))
    a[:] = np.nan
    dataFrame = None
    parameters = ['alpha0', 'beta0','alpha','beta','gamma']
    for params in parameters:
        iter = ['iter_'+str(i) for i in range(num_iters)]
        pdindex = pd.MultiIndex.from_product([[params], iter],
                                             names=['parameters', 'runs']) 
        frame = pd.DataFrame(a, columns = pdindex,index = range(0,num_runs))
        dataFrame = pd.concat([dataFrame,frame],axis=1)
    return dataFrame

def simulate_mediation(df,M,params_df,model,algo,num_subs,batch_size,epochs,n,n_runs,iterations):
    """
    """
    early_stopping=True
    # Initialize z with some phi
    print("Using intial random model parameters")
#     if algo == 'svr':
#         z = svr.predict(M.flatten())
    z = model.predict(M) 
    try:
        z = np.concatenate(z)
    except:
        pass
    # plot_scatter(z,df.m,labels=['z','m'])
    
    for i in range(0,iterations):
        print('Starting iteration... %s'%(i+1))
        #Check for sign change
        if np.corrcoef(z,df.Y)[0,1] < 0 :
            z = z*(-1)
        # Check for scaling
        z= zscore(z)

        lm = smf.ols(formula='z ~ X', data=df).fit()
        alpha0 = lm.params.loc['Intercept']
        alph = lm.params.loc['X'] 

        lm = smf.ols(formula='Y ~ z + X', data=df).fit()
        beta0 = lm.params.Intercept 
        bet = lm.params.z
        gam = lm.params.X 
        resid_std = np.std(lm.resid)
        e = df.Y - beta0 - (df.X*gam)
        h = alpha0 + df.X*alph
        d = (((bet*e)+h)/((bet**2)+1))

        if algo== 'svr':
            model = auxiliaryfunctions.create_svr_model(M,d)
            z = model.predict(M)
        else:
            adam = Adam(lr=0.001, decay=0.03)
            model.compile(loss='mean_absolute_error',optimizer=adam)
            if early_stopping:
                es = EarlyStopping(monitor='val_loss', mode='min', verbose=1,patience=20)
                history = model.fit(M,d,batch_size=batch_size,epochs=epochs,verbose=1,callbacks=[es],
                                  shuffle=True,validation_split = 0.3)
            else:
                history = model.fit(M,d,batch_size=batch_size,epochs=epochs,verbose=1,
                              shuffle=True,validation_split = 0.3)
            z = model.predict(M)
       
        params_df.loc[n_runs]['alpha0','iter_'+str(i)]=alpha0
        params_df.loc[n_runs]['beta0','iter_'+str(i)]=beta0
        params_df.loc[n_runs]['beta','iter_'+str(i)]=bet
        params_df.loc[n_runs]['gamma','iter_'+str(i)]=gam
        params_df.loc[n_runs]['alpha','iter_'+str(i)]=alph

        try:
            z = np.concatenate(z)
        except:
            pass
       
    return params_df,z


In [6]:
ls -ltrh ../results/simulation-2-results/


total 964K
-rw-rw-r-- 1 ubuntu ubuntu 124K Dec 10 10:59 simulation-2-image-size-8-svr.xlsx
-rw-rw-r-- 1 ubuntu ubuntu 124K Dec 11 11:04 simulation-2-image-size-32-svr.xlsx
-rw-rw-r-- 1 ubuntu ubuntu 121K Dec 12 04:49 simulation-2-image-size-64-shallow.xlsx
-rw-rw-r-- 1 ubuntu ubuntu 121K Dec 12 18:58 simulation-2-image-size-8-shallow.xlsx
-rw-rw-r-- 1 ubuntu ubuntu  71K Dec 13 04:45 simulation-2-image-size-32-shallow.xlsx
-rw-rw-r-- 1 ubuntu ubuntu  86K Dec 13 16:08 simulation-2-image-size-32-shallow-part-1.xlsx
-rw-rw-r-- 1 ubuntu ubuntu  65K Dec 16 06:57 simulation-2-image-size-32-deep.xlsx
-rw-rw-r-- 1 ubuntu ubuntu  83K Dec 17 18:25 simulation-2-image-size-8-deep.xlsx
-rw-rw-r-- 1 ubuntu ubuntu  95K Dec 17 19:08 simulation-2-image-size-64-svr.xlsx
-rw-rw-r-- 1 ubuntu ubuntu  59K Dec 17 19:18 simulation-2-image-size-32-deep-part1.xlsx


parameters       alpha0   Unnamed: 2   Unnamed: 3   Unnamed: 4  \
0        runs       iter_0       iter_1       iter_2       iter_3   
1         NaN          NaN          NaN          NaN          NaN   
2           0  0.000915156   0.00595582   0.00569645   0.00656604   
3           1  -0.00547069   -0.0143827   -0.0147859   -0.0146828   
4           2  -0.00196018  -0.00541597  -0.00629073    -0.006582   
5           3  0.000567865 -0.000324903   0.00225347   0.00236391   
6           4 -0.000849919  -0.00936129   -0.0116077   -0.0118103   
7           5 -0.000230804  -0.00020669  -0.00160922  -0.00163365   
8           6  -0.00070383 -0.000958431  0.000669363    -0.005061   
9           7   -0.0017206  -0.00430184  -0.00441935  -0.00447851   
10          8   0.00351756 -0.000328957   0.00498508   0.00211051   
11          9    0.0022409   0.00366061   0.00876563    0.0089891   
12         10  0.000524406  0.000305433   0.00191227   0.00197388   
13         11  -0.00025938  -0.00022595  -0.00182508  -0.00187563   
14         12  -0.00195525  -0.00347203  -0.00506205 -0.000252114   
15         13 -0.000190585 -0.000877482 -0.000994884 -0.000999912   
16         14 -4.78708e-06  0.000319513  2.42814e-05  0.000383733   
17         15  0.000403596   0.00833917   0.00987401   0.00985252   
18         16  -0.00159716  -0.00623398  -0.00767707  -0.00777314   
19         17  0.000164638 -0.000859834 -0.000911288 -0.000955135   
20         18  -0.00176348 -0.000771768  -0.00649767  -0.00656403   
21         19    0.0024337   0.00477082   0.00546007   0.00572099   
22         20   0.00123911   0.00114233   0.00204274   0.00207899   
23         21  0.000195144  0.000188568  0.000193319   0.00167967   
24         22  7.04852e-05  -0.00263271  -0.00291077  -0.00284526   
25         23 -0.000232962   -0.0094942   -0.0111655   -0.0115896   
26         24  -0.00143048  -0.00464438  -0.00493403  -0.00495184   
27         25   0.00158772   0.00223038   0.00157996   0.00761877   
28         26  -0.00359081  -0.00385442  -0.00620895  -0.00775759   
29         27 -0.000438502  -0.00107713  -0.00125033  -0.00128137   
30         28  0.000968837   0.00161724    0.0019697   0.00204468   
31         29  -0.00162801   -0.0030923  -0.00551624  -0.00564938   
32         30  -0.00022367 -0.000162481 -0.000543951  -0.00168088   
33         31  1.10159e-06 -1.72193e-05 -2.05565e-05 -2.05479e-05   
34         32 -0.000285835  -0.00352596 -0.000651528  -0.00509723   
35         33 -0.000417884   0.00123977   0.00375292    0.0038083   
36         34   0.00218762   0.00620535   0.00667285   0.00676946   
37         35 -0.000114168  -0.00178033 -7.21425e-05  -0.00205919   
38         36  0.000628613    0.0011191   0.00194372    0.0020408   
39         37          NaN          NaN          NaN          NaN   

     Unnamed: 5   Unnamed: 6   Unnamed: 7   Unnamed: 8   Unnamed: 9  ...  \
0        iter_4       iter_5       iter_6       iter_7       iter_8  ...   
1           NaN          NaN          NaN          NaN          NaN  ...   
2    0.00649151   0.00647657    0.0064724   0.00656461    0.0065914  ...   
3      -0.01471   -0.0147901   -0.0147964   -0.0146999   -0.0147615  ...   
4   -0.00655682  -0.00661856  -0.00661956  -0.00660091  -0.00661053  ...   
5     0.0022946   0.00232802   0.00229621   0.00230978   0.00230961  ...   
6    -0.0118569   -0.0118167   -0.0117269   -0.0118866    -0.011875  ...   
7   -0.00165734  -0.00165221  -0.00167632   -0.0016713  -0.00166656  ...   
8   -0.00524106   -0.0051921  -0.00525198  -0.00522242  -0.00523236  ...   
9   -0.00456465  -0.00455831  -0.00455094  -0.00455239  -0.00455044  ...   
10   0.00511219   0.00517354   0.00529049   0.00530712   0.00531717  ...   
11    0.0090901    0.0089636   0.00903072   0.00906258    0.0091037  ...   
12   0.00199543   0.00195549   0.00198262   0.00196032   0.00198244  ...   
13  -0.00189701  -0.00187748  -0.00187119  -0.00187285  -0.00187025  ...   
14  -0.00491175   -0.0051242    -

In [12]:
os.environ["CUDA_VISIBLE_DEVICES"]="0"

for n in new_shape:
    start = 62
    output_df = create_empty_df(num_runs,num_iters)
    for runs in range(start,num_runs):
        K.clear_session()
        print("Running simulation for image shape %s starting with %s runs"%(n,runs+1))
    # simulate the dataset
        df,mediator,z = auxiliaryfunctions.simulate_dataset(num_subs,resize= True,
                                          new_shape=n,algo=algo,visualize=False,alpha=0.2)
        # create a model 
        if algo == 'svr':
            model = auxiliaryfunctions.create_svr_model(mediator,df.m)
        elif algo== 'shallow':
            input_shape = (n[0],n[1]*4,1)
            model = auxiliaryfunctions.create_shallow_model2D(input_shape=input_shape)
        else:
            input_shape = (n[0],n[1]*4,1)
            model = auxiliaryfunctions.create_deep_model2D(input_shape=input_shape)

        params_df,z_final = simulate_mediation(df,mediator,output_df,
                                      model,algo,n,batch_size,epochs,
                                      n,runs,num_iters)
        params_df.to_excel(os.path.join(result_path,'simulation-2-image-size-'+str(n[0])+'-'+algo+'-part2.xlsx'))

Running simulation for image shape [32, 32] starting with 63 runs
Using intial random model parameters
Starting iteration... 1
Epoch 1/1000
175/175 [==============================] - 2s 10ms/step - loss: 78.4666 - val_loss: 1.0528
Epoch 2/1000
175/175 [==============================] - 1s 7ms/step - loss: 2.6573 - val_loss: 1.0322
Epoch 3/1000
175/175 [==============================] - 1s 7ms/step - loss: 2.5199 - val_loss: 1.0329
Epoch 4/1000
175/175 [==============================] - 1s 7ms/step - loss: 2.6098 - val_loss: 1.0324
Epoch 5/1000
175/175 [==============================] - 1s 7ms/step - loss: 2.5994 - val_loss: 1.0298
Epoch 6/1000
175/175 [==============================] - 1s 7ms/step - loss: 2.6307 - val_loss: 1.0265
Epoch 7/1000
175/175 [==============================] - 1s 7ms/step - loss: 2.4557 - val_loss: 1.0276
Epoch 8/1000
175/175 [==============================] - 1s 7ms/step - loss: 2.4692 - val_loss: 1.0271
Epoch 9/1000
175/175 [==============================] -

175/175 [==============================] - 1s 7ms/step - loss: 2.2843 - val_loss: 0.9211
Epoch 80/1000
175/175 [==============================] - 1s 7ms/step - loss: 2.3444 - val_loss: 0.9016
Epoch 81/1000
175/175 [==============================] - 1s 7ms/step - loss: 2.2223 - val_loss: 0.8914
Epoch 82/1000
175/175 [==============================] - 1s 7ms/step - loss: 2.2773 - val_loss: 0.8985
Epoch 83/1000
175/175 [==============================] - 1s 7ms/step - loss: 2.1904 - val_loss: 0.9554
Epoch 84/1000
175/175 [==============================] - 1s 8ms/step - loss: 2.2161 - val_loss: 1.0216
Epoch 85/1000
175/175 [==============================] - 1s 7ms/step - loss: 2.2159 - val_loss: 0.8985
Epoch 86/1000
175/175 [==============================] - 1s 7ms/step - loss: 2.3159 - val_loss: 1.0296
Epoch 87/1000
175/175 [==============================] - 1s 8ms/step - loss: 2.3216 - val_loss: 0.9242
Epoch 88/1000
175/175 [==============================] - 1s 8ms/step - loss: 2.2595 - v

Epoch 158/1000
175/175 [==============================] - 2s 12ms/step - loss: 2.0959 - val_loss: 0.8005
Epoch 159/1000
175/175 [==============================] - 2s 12ms/step - loss: 2.0959 - val_loss: 0.8194
Epoch 160/1000
175/175 [==============================] - 2s 12ms/step - loss: 2.0798 - val_loss: 0.7968
Epoch 161/1000
175/175 [==============================] - 2s 12ms/step - loss: 2.0249 - val_loss: 0.7901
Epoch 162/1000
175/175 [==============================] - 2s 12ms/step - loss: 2.0034 - val_loss: 0.8048
Epoch 163/1000
175/175 [==============================] - 2s 12ms/step - loss: 2.0268 - val_loss: 0.7842
Epoch 164/1000
175/175 [==============================] - 2s 12ms/step - loss: 2.1054 - val_loss: 0.7789
Epoch 165/1000
175/175 [==============================] - 2s 12ms/step - loss: 2.0513 - val_loss: 0.7863
Epoch 166/1000
175/175 [==============================] - 2s 12ms/step - loss: 2.0890 - val_loss: 0.7749
Epoch 167/1000
175/175 [==============================]

175/175 [==============================] - 2s 11ms/step - loss: 2.0298 - val_loss: 0.7238
Epoch 237/1000
175/175 [==============================] - 2s 11ms/step - loss: 1.9369 - val_loss: 0.7139
Epoch 238/1000
175/175 [==============================] - 2s 12ms/step - loss: 1.9350 - val_loss: 0.7120
Epoch 239/1000
175/175 [==============================] - 2s 12ms/step - loss: 2.0242 - val_loss: 0.7346
Epoch 240/1000
175/175 [==============================] - 2s 12ms/step - loss: 1.9681 - val_loss: 0.7239
Epoch 241/1000
175/175 [==============================] - 2s 12ms/step - loss: 1.9033 - val_loss: 0.7217
Epoch 00241: early stopping
Starting iteration... 2
Epoch 1/1000
175/175 [==============================] - 3s 17ms/step - loss: 6.5659 - val_loss: 0.9179
Epoch 2/1000
175/175 [==============================] - 2s 12ms/step - loss: 2.2589 - val_loss: 0.9182
Epoch 3/1000
175/175 [==============================] - 2s 12ms/step - loss: 2.1651 - val_loss: 0.9184
Epoch 4/1000
175/175 [==

175/175 [==============================] - 1s 8ms/step - loss: 1.8622 - val_loss: 0.8814
Epoch 74/1000
175/175 [==============================] - 1s 8ms/step - loss: 1.8588 - val_loss: 0.9038
Epoch 75/1000
175/175 [==============================] - 1s 8ms/step - loss: 1.8717 - val_loss: 0.8847
Epoch 76/1000
175/175 [==============================] - 1s 8ms/step - loss: 1.7400 - val_loss: 0.8695
Epoch 77/1000
175/175 [==============================] - 1s 8ms/step - loss: 1.8778 - val_loss: 0.8622
Epoch 78/1000
175/175 [==============================] - 1s 8ms/step - loss: 1.8541 - val_loss: 0.8571
Epoch 79/1000
175/175 [==============================] - 1s 8ms/step - loss: 1.8485 - val_loss: 0.8784
Epoch 80/1000
175/175 [==============================] - 1s 8ms/step - loss: 1.8746 - val_loss: 0.8628
Epoch 81/1000
175/175 [==============================] - 1s 8ms/step - loss: 1.8908 - val_loss: 0.8536
Epoch 82/1000
175/175 [==============================] - 1s 8ms/step - loss: 1.8507 - v

...

175/175 [==============================] - 1s 8ms/step - loss: 0.2757 - val_loss: 0.2439
Epoch 36/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2620 - val_loss: 0.2410
Epoch 37/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2725 - val_loss: 0.2407
Epoch 38/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2733 - val_loss: 0.2478
Epoch 39/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2533 - val_loss: 0.2544
Epoch 40/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2720 - val_loss: 0.2436
Epoch 41/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2776 - val_loss: 0.2405
Epoch 00041: early stopping
Starting iteration... 13
Epoch 1/1000
175/175 [==============================] - 2s 10ms/step - loss: 0.4780 - val_loss: 0.4006
Epoch 2/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.3616 - val_loss: 0.3261
Epoch 3/1000
175/175 [=============

Epoch 32/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2762 - val_loss: 0.2494
Epoch 33/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2718 - val_loss: 0.2507
Epoch 34/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2763 - val_loss: 0.2406
Epoch 35/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2713 - val_loss: 0.2431
Epoch 36/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2675 - val_loss: 0.2398
Epoch 37/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2721 - val_loss: 0.2386
Epoch 38/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2716 - val_loss: 0.2464
Epoch 39/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2572 - val_loss: 0.2486
Epoch 40/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2698 - val_loss: 0.2444
Epoch 41/1000
175/175 [==============================] - 1s 8ms/step - lo

175/175 [==============================] - 1s 8ms/step - loss: 0.2638 - val_loss: 0.2403
Epoch 29/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2733 - val_loss: 0.2388
Epoch 30/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2576 - val_loss: 0.2466
Epoch 31/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2640 - val_loss: 0.2384
Epoch 32/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2708 - val_loss: 0.2461
Epoch 33/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2724 - val_loss: 0.2520
Epoch 34/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2679 - val_loss: 0.2396
Epoch 35/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2677 - val_loss: 0.2414
Epoch 36/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2593 - val_loss: 0.2389
Epoch 37/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2666 - v

Epoch 26/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2640 - val_loss: 0.2449
Epoch 27/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2530 - val_loss: 0.2398
Epoch 28/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2645 - val_loss: 0.2400
Epoch 29/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2750 - val_loss: 0.2387
Epoch 30/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2523 - val_loss: 0.2417
Epoch 31/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2590 - val_loss: 0.2418
Epoch 32/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2659 - val_loss: 0.2455
Epoch 33/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2670 - val_loss: 0.2487
Epoch 34/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2642 - val_loss: 0.2401
Epoch 35/1000
175/175 [==============================] - 1s 8ms/step - lo

175/175 [==============================] - 1s 8ms/step - loss: 0.2702 - val_loss: 0.2380
Epoch 26/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2630 - val_loss: 0.2434
Epoch 27/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2538 - val_loss: 0.2355
Epoch 28/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2674 - val_loss: 0.2401
Epoch 29/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2711 - val_loss: 0.2371
Epoch 30/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2555 - val_loss: 0.2408
Epoch 31/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2635 - val_loss: 0.2398
Epoch 32/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2672 - val_loss: 0.2481
Epoch 33/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2728 - val_loss: 0.2440
Epoch 34/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.2642 - v

In [18]:
n

[8, 8]

In [5]:
params_df.head(100)

parameters    alpha0                                                    \
runs          iter_0    iter_1    iter_2    iter_3    iter_4    iter_5   
0           0.000915  0.005956  0.005696  0.006566  0.006492  0.006477   
1          -0.005471 -0.014383 -0.014786 -0.014683 -0.014710 -0.014790   
2          -0.001960 -0.005416 -0.006291 -0.006582 -0.006557 -0.006619   
3           0.000568 -0.000325  0.002253  0.002364  0.002295  0.002328   
4          -0.000850 -0.009361 -0.011608 -0.011810 -0.011857 -0.011817   
..               ...       ...       ...       ...       ...       ...   
95               NaN       NaN       NaN       NaN       NaN       NaN   
96               NaN       NaN       NaN       NaN       NaN       NaN   
97               NaN       NaN       NaN       NaN       NaN       NaN   
98               NaN       NaN       NaN       NaN       NaN       NaN   
99               NaN       NaN       NaN       NaN       NaN       NaN   

parameters                                          ...     gamma            \
runs          iter_6    iter_7    iter_8    iter_9  ...   iter_10   iter_11   
0           0.006472  0.006565  0.006591  0.006630  ...  5.008365  5.001208   
1          -0.014796 -0.014700 -0.014761 -0.014800  ...  5.018139  5.014577   
2          -0.006620 -0.006601 -0.006611 -0.006596  ...  5.069428  5.066790   
3           0.002296  0.002310  0.002310  0.002289  ...  5.011432  5.016236   
4          -0.011727 -0.011887 -0.011875 -0.011850  ...  5.002707  4.997598   
..               ...       ...       ...       ...  ...       ...       ...   
95               NaN       NaN       NaN       NaN  ...       NaN       NaN   
96               NaN       NaN       NaN       NaN  ...       NaN       NaN   
97               NaN       NaN       NaN       NaN  ...       NaN       NaN   
98               NaN       NaN       NaN       NaN  ...       NaN       NaN   
99               NaN       NaN       NaN       NaN  ...       NaN       NaN   

parameters                                                              \
runs         iter_12   iter_13   iter_14   iter_15   iter_16   iter_17   
0           4.999168  4.996739  4.994244  4.996282  4.994416  4.996031   
1           5.012993  5.012893  5.004050  5.000116  4.998129  4.995672   
2           5.066708  5.061213  5.066157  5.064019  5.057355  5.057891   
3           5.014986  5.014096  5.013874  5.016520  5.015937  5.018543   
4           4.997377  4.989784  4.984232  4.982610  4.984709  4.982805   
..               ...       ...       ...       ...       ...       ...   
95               NaN       NaN       NaN       NaN       NaN       NaN   
96               NaN       NaN       NaN       NaN       NaN       NaN   
97               NaN       NaN       NaN       NaN       NaN       NaN   
98               NaN       NaN       NaN       NaN       NaN       NaN   
99               NaN       NaN       NaN       NaN       NaN       NaN   

parameters                      
runs         iter_18   iter_19  
0           4.996936  4.990617  
1           5.000257  4.996669  
2           5.056036  5.052867  
3           5.017405  5.016720  
4           4.981543  4.976197  
..               ...       ...  
95               NaN       NaN  
96               NaN       NaN  
97               NaN       NaN  
98               NaN       NaN  
99               NaN       NaN  

[100 rows x 100 columns]

In [1]:
!nvidia-smi

Fri Nov  6 18:35:25 2020       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 450.51.06    Driver Version: 450.51.06    CUDA Version: 11.0     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla V100-SXM2...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   42C    P0    46W / 300W |      0MiB / 16160MiB |      4%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
|   1  Tesla V100-SXM2...  Off  | 00000000:00:05.0 Off |                    0 |
| N/A   